In [1]:
from datasets import load_dataset, Dataset
import pandas as pd
import numpy as np
from PIL import Image
from transformers import TrOCRProcessor, VisionEncoderDecoderModel
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import torch
from torch.nn.utils.rnn import pad_sequence
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments, default_data_collator, EncoderDecoderModel, AutoTokenizer
from torch.utils.data import Dataset, DataLoader
import os
from datasets import load_metric

c:\Users\ASUS\anaconda3\Lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  torch.utils._pytree._register_pytree_node(
c:\Users\ASUS\anaconda3\Lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  torch.utils._pytree._register_pytree_node(


In [2]:
test_df = pd.read_csv(r'C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\written_name_test_v2.csv')
test_df=test_df.head(100)

In [3]:
test_df

FILENAME  IDENTITY
0   C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...     KEVIN
1   C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...  CLOTAIRE
2   C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...      LENA
3   C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...     JULES
4   C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...   CHERPIN
..                                                ...       ...
95  C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...   VENTURA
96  C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...     NDOUR
97  C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...      LISE
98  C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...   JUSTINE
99  C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\tes...       LEO

[100 rows x 2 columns]

In [4]:
cer_metric = load_metric("cer")


C:\Users\ASUS\AppData\Local\Temp\ipykernel_34364\1691216033.py:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  cer_metric = load_metric("cer")


In [5]:
MODEL_PATH = r"C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\DATA _TrOCR\checkpoint-6000"
model = VisionEncoderDecoderModel.from_pretrained(MODEL_PATH)
processor = TrOCRProcessor.from_pretrained('microsoft/trocr-base-handwritten')


In [ ]:
model.to("cuda" if torch.cuda.is_available() else "cpu")

In [6]:
class CustomDataset(Dataset):
    def __init__(self, root_dir, df, processor, max_target_length=128):
        self.root_dir = root_dir
        self.df = df
        self.processor = processor
        self.max_target_length = max_target_length
        self.image_paths = self._collect_image_paths()
        print("Image paths collected:", self.image_paths)

    def _collect_image_paths(self):
        image_paths = {}
        for root, dirs, files in os.walk(self.root_dir):
            for file in files:
                if file.endswith(('.tif', '.jpg', '.png')):
                    image_paths[file] = os.path.join(root, file)
        return image_paths

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        print(f"Processing index: {idx}")
        
        full_file_path = self.df['FILENAME'].iloc[idx]
        text = self.df['IDENTITY'].iloc[idx]
        
        text = str(text)
        file_name = os.path.basename(full_file_path)
        image_path = self.image_paths.get(file_name)

        print(f"Full file path: {full_file_path}, File name: {file_name}, Image path: {image_path}")

        if image_path is None:
            raise FileNotFoundError(f"Image {file_name} not found in {self.root_dir}")

        image = Image.open(image_path).convert("RGB")
        pixel_values = self.processor(image, return_tensors="pt").pixel_values
        labels = self.processor.tokenizer(text, padding="max_length", max_length=self.max_target_length).input_ids
        labels = [label if label != self.processor.tokenizer.pad_token_id else -100 for label in labels]

        encoding = {"pixel_values": pixel_values.squeeze(), "labels": torch.tensor(labels)}
        return encoding

# Initialize the test dataset
test_dataset = CustomDataset(
    root_dir=r'C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\test',  # Update this to your test images directory
    df=test_df,
    processor=processor
)

def get_predictions(model, dataloader, processor):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)
    model.eval()
    predictions = []
    references = []
    with torch.no_grad():
        for batch in dataloader:
            input_ids = batch["pixel_values"].to(device)
            outputs = model.generate(input_ids)
            pred_str = processor.batch_decode(outputs, skip_special_tokens=True)
            label_ids = batch["labels"].cpu().numpy()
            label_ids[label_ids == -100] = processor.tokenizer.pad_token_id
            label_str = processor.batch_decode(label_ids, skip_special_tokens=True)
            predictions.extend(pred_str)
            references.extend(label_str)
    return predictions, references

test_loader = DataLoader(test_dataset, batch_size=1, shuffle=False)

predictions, references = get_predictions(model, test_loader, processor)

cer_metric = load_metric("cer")
cer = cer_metric.compute(predictions=predictions, references=references)
print(f'Character Error Rate: {cer}')

def display_results(test_df, predictions, cer):
    cer_metric = load_metric("cer")
    cer_values = []
    
    for i in range(len(predictions)):
        image_path = test_df['FILENAME'].iloc[i]
        ground_truth = test_df['IDENTITY'].iloc[i]
        prediction = predictions[i]

        # image = Image.open(image_path)
        # plt.imshow(image)
        # plt.axis('off')
        # plt.show()

        # print(f"Ground Truth: {ground_truth}")
        # print(f"OCR Text: {prediction}")
        # print(f"Character Error Rate: {cer}")
        # print("\n")

# Display results

display_results(test_df, predictions, cer)
print("DISPLAY", predictions)
test_df['prediction'] = predictions
test_df['cer'] = cer_values

output_csv_path = r"C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\test_df.csv"
test_df.to_csv(output_csv_path, index=False)

print(f"CSV with CER values saved to: {output_csv_path}")


Image paths collected: {'TEST_0001.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0001.jpg', 'TEST_0002.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0002.jpg', 'TEST_0003.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0003.jpg', 'TEST_0004.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0004.jpg', 'TEST_0005.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0005.jpg', 'TEST_0006.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0006.jpg', 'TEST_0007.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0007.jpg', 'TEST_0008.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0008.jpg', 'TEST_0009.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0009.jpg', 'TEST_0010.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0010.jpg', 'TEST_0011.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0011.jpg

NameError: name 'cer_values' is not defined

In [7]:

class CustomDataset(Dataset):
    def __init__(self, root_dir, df, processor, max_target_length=128):
        self.root_dir = root_dir
        self.df = df
        self.processor = processor
        self.max_target_length = max_target_length
        self.image_paths = self._collect_image_paths()
        print("Image paths collected:", self.image_paths)

    def _collect_image_paths(self):
        image_paths = {}
        for root, dirs, files in os.walk(self.root_dir):
            for file in files:
                if file.endswith(('.tif', '.jpg', '.png')):
                    image_paths[file] = os.path.join(root, file)
        return image_paths

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        print(f"Processing index: {idx}")
        
        full_file_path = self.df['FILENAME'].iloc[idx]
        text = self.df['IDENTITY'].iloc[idx]
        
        text = str(text)
        file_name = os.path.basename(full_file_path)
        image_path = self.image_paths.get(file_name)

        print(f"Full file path: {full_file_path}, File name: {file_name}, Image path: {image_path}")

        if image_path is None:
            raise FileNotFoundError(f"Image {file_name} not found in {self.root_dir}")

        image = Image.open(image_path).convert("RGB")
        pixel_values = self.processor(image, return_tensors="pt").pixel_values
        labels = self.processor.tokenizer(text, padding="max_length", max_length=self.max_target_length).input_ids
        labels = [label if label != self.processor.tokenizer.pad_token_id else -100 for label in labels]

        encoding = {"pixel_values": pixel_values.squeeze(), "labels": torch.tensor(labels)}
        return encoding

# Initialize the test dataset
test_dataset = CustomDataset(
    root_dir=r'C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\test',  # Update this to your test images directory
    df=test_df,
    processor=processor
)

def get_predictions(model, dataloader, processor):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)
    model.eval()
    predictions = []
    references = []
    with torch.no_grad():
        for batch in dataloader:
            input_ids = batch["pixel_values"].to(device)
            outputs = model.generate(input_ids)
            pred_str = processor.batch_decode(outputs, skip_special_tokens=True)
            label_ids = batch["labels"].cpu().numpy()
            label_ids[label_ids == -100] = processor.tokenizer.pad_token_id
            label_str = processor.batch_decode(label_ids, skip_special_tokens=True)
            predictions.extend(pred_str)
            references.extend(label_str)
    return predictions, references

test_loader = DataLoader(test_dataset, batch_size=1, shuffle=False)

predictions, references = get_predictions(model, test_loader, processor)

def display_results(test_df, predictions):
    cer_metric = load_metric("cer")
    cer_values = []
    
    for i in range(len(predictions)):
        image_path = test_df['FILENAME'].iloc[i]
        ground_truth = test_df['IDENTITY'].iloc[i]
        prediction = predictions[i]

        # Compute CER for this prediction
        cer = cer_metric.compute(predictions=[prediction], references=[ground_truth])
        cer_values.append(cer)

        # Uncomment below lines to display images and results if needed
        # image = Image.open(image_path)
        # plt.imshow(image)
        # plt.axis('off')
        # plt.show()

        # print(f"Ground Truth: {ground_truth}")
        # print(f"OCR Text: {prediction}")
        # print(f"Character Error Rate: {cer}")
        # print("\n")

    test_df['prediction'] = predictions
    test_df['cer'] = cer_values

    return test_df

# Display results and update DataFrame
test_df = display_results(test_df, predictions)
print("DISPLAY", predictions)

output_csv_path = r"C:\Users\ASUS\OneDrive\Desktop\TROCR_MODEL\test_df.csv"
test_df.to_csv(output_csv_path, index=False)

print(f"CSV with CER values saved to: {output_csv_path}")


Image paths collected: {'TEST_0001.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0001.jpg', 'TEST_0002.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0002.jpg', 'TEST_0003.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0003.jpg', 'TEST_0004.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0004.jpg', 'TEST_0005.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0005.jpg', 'TEST_0006.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0006.jpg', 'TEST_0007.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0007.jpg', 'TEST_0008.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0008.jpg', 'TEST_0009.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0009.jpg', 'TEST_0010.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0010.jpg', 'TEST_0011.jpg': 'C:\\Users\\ASUS\\OneDrive\\Desktop\\TROCR_MODEL\\test\\TEST_0011.jpg